In [1]:
# LIBRARIES #

import numpy as np

import SimpleITK

from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.models import LinearColorMapper, BasicTicker, ColorBar, Plot, CustomJS, ColumnDataSource, Rect
from bokeh.layouts import row, gridplot, column
from bokeh.models.widgets import Slider

output_notebook()

Loading BokehJS ...

In [2]:
# INPUT PARAMETERS #

m_filename = 'G:/Commun/PHYSICIENS/CQ/CQ_interne_BV/Cyberknife M6/CQ mensuel/2019/2019 02 19/champs lumineux - irradie.tif'

m_coefA = 1774.1   #x3
m_coefB = -3907.8  #x2
m_coefC = 3276.7   #x
m_coefD = -935.12

m_dosemax = 850.0 #cGy


In [3]:
# READS THE IMAGE AND CONVERTS IT TO DOSE #

def readAndConvertImgToDose(filename, coefs):
    # reads the image using simpleITK:
    img = SimpleITK.ReadImage(filename)
    sizex = img.GetWidth()
    sizey = img.GetHeight()
    array = SimpleITK.GetArrayFromImage(img)
    
    # replaces every 65535 value in array with 65534 to avoid division by zero:
    array[array==65535]=65534
    
    # converts in optical density
    dor = -np.log10(array[:,:,0]/65535.0)
    dob = -np.log10(array[:,:,2]/65535.0)
    
    # red channel over blue channel:
    rsb = dor/dob
#    rsb[rsb>1.3] = 1.3

    # converting in dose:
    dose = coefs[0]*rsb**3 + coefs[1]*rsb**2 + coefs[2]*rsb + coefs[3]
    dose[dose>m_dosemax] = m_dosemax
    
    return dose, sizex, sizey

In [4]:
# READS THE IMAGE AND CONVERTS IT TO RGBA IMG #

def readAndConvertImgToRGBA(filename, coefs):
    # reads the image using simpleITK:
    img = SimpleITK.ReadImage(filename)
    sizex = img.GetWidth()
    sizey = img.GetHeight()
    array = SimpleITK.GetArrayFromImage(img)
    
    # creates a new rgba img and copy the tiff values in it
    img = np.empty((sizey,sizex), dtype=np.uint32)
    view = img.view(dtype=np.uint8).reshape((sizey, sizex, 4))
    view[:,:,0] = array[:,:,0]/65535.0*255.0
    view[:,:,1] = array[:,:,1]/65535.0*255.0
    view[:,:,2] = array[:,:,2]/65535.0*255.0
    view[:,:,3] = 255

    return img, sizex, sizey

In [5]:
# PLOTS IMAGE AND PROFILES #


# Line profiles to draw:
ImgPlotWidth = 600


# Reads the image and convert it to dose:
coefs = [m_coefA, m_coefB, m_coefC, m_coefD]

doseimg, sizex, sizey = readAndConvertImgToDose(m_filename, coefs)
maxdose = int(np.amax(doseimg))

print('Image dimension (in pixels):', sizex, 'x', sizey)
print('Dose max:', maxdose, 'cGy')


# Displays the dose image (p1):
color_mapper = LinearColorMapper(palette="Viridis256", low=0, high=maxdose)

color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(),
                     label_standoff=12, border_line_color=None, location=(0,0),
                     title='Dose cGy')

p1 = figure(plot_width=int(ImgPlotWidth*1.1), plot_height=int(ImgPlotWidth*sizey/sizex), x_range=(0,sizex), y_range=(0,sizey), 
            title="Dose image", toolbar_location="above")

l1_source = ColumnDataSource(data=dict(x=[0,int(sizex)], y=[int(sizey/2),int(sizey/2)]))
l2_source = ColumnDataSource(data=dict(x=[int(sizex/2), int(sizex/2)], y=[0, int(sizey)]))

p1.image(image=[doseimg], x=[0], y=[0], dw=[sizex], dh=[sizey], color_mapper=color_mapper)
p1.line('x', 'y', source=l1_source, line_width=2, line_color=(255, 255, 255, 0.7))
p1.line('x', 'y', source= l2_source, line_width=2, line_color=(255, 255, 255, 0.7))

p1.add_layout(color_bar, 'right')


# Displays the zoomed window:
p1b_source = ColumnDataSource({'x': [], 'y': [], 'width': [], 'height': []})

jscode="""
    var data = source.data;
    var start = cb_obj.start;
    var end = cb_obj.end;
    data['%s'] = [start + (end - start) / 2];
    data['%s'] = [end - start];
    source.change.emit();
"""

p1.x_range.callback = CustomJS(args=dict(source=p1b_source), code=jscode % ('x', 'width'))
p1.y_range.callback = CustomJS(args=dict(source=p1b_source), code=jscode % ('y', 'height'))

p1b = figure(title='Zoom Window', plot_width=int(ImgPlotWidth*0.5), plot_height=int(ImgPlotWidth*0.5*sizey/sizex), 
             x_range=(0,sizex), y_range=(0,sizey), tools='')
p1b.image(image=[doseimg], x=[0], y=[0], dw=[sizex], dh=[sizey], color_mapper=color_mapper)
rect = Rect(x='x', y='y', width='width', height='height', fill_alpha=0.1,
            line_color='white', fill_color='white')
p1b.add_glyph(p1b_source, rect)

p1b.xaxis.major_tick_line_color = None  # turn off x-axis major ticks
p1b.xaxis.minor_tick_line_color = None  # turn off x-axis minor ticks
p1b.yaxis.major_tick_line_color = None  # turn off y-axis major ticks
p1b.yaxis.minor_tick_line_color = None  # turn off y-axis minor ticks
p1b.xaxis.major_label_text_color = None  # turn off x-axis tick labels leaving space
p1b.yaxis.major_label_text_color = None  # turn off y-axis tick labels leaving space 

# Displays profiles:
maxdose_x = np.amax(doseimg[:,:])
p2_source = ColumnDataSource(data=dict(x=np.arange(0, sizex, 1), y=doseimg[int(sizey/2)]))
p2 = figure(plot_width=480, plot_height=300, x_range=(0,sizex), y_range=(0,maxdose_x), 
            title="Horizontal dose profile", toolbar_location="above")
p2.line('x', 'y', source=p2_source, line_color="#2690d4", line_width=3, line_alpha=1.0)

p3 = figure(plot_width=480, plot_height=300, x_range=(0,sizey), y_range=(0,maxdose_x), 
            title="Vertical dose profile", toolbar_location="above")
p3_source = ColumnDataSource(data=dict(x=np.arange(0, sizey, 1), y=doseimg[:,int(sizex/2)]))
p3.line('x', 'y', source=p3_source, line_color="#2690d4", line_width=3, line_alpha=1.0)


# Callback functions called when the sliders are changed
callback1 = CustomJS(args=dict(source1=l1_source, source2=p2_source), code="""
    var f = horizontalPosSlider.value;

    var data1 = source1.data;
    var y1 = data1['y'];
    y1[0] = f;
    y1[1] = f;
    source1.change.emit();

    var data2 = source2.data;
    var x2 = data2['x'];
    var y2 = data2['y'];
    for (i = 0; i < x2.length; i++) {
        y2[i] = img[f][i];
    }    
    source2.change.emit();
""")


callback2 = CustomJS(args=dict(source1=l2_source, source2=p3_source), code="""
    var f = verticalPosSlider.value;

    var data1 = source1.data;
    var x1 = data1['x'];
    x1[0] = f;
    x1[1] = f;
    source1.change.emit();
    
    var data2 = source2.data;
    var x2 = data2['x'];
    var y2 = data2['y'];
    for (i = 0; i < x2.length; i++) {
        y2[i] = img[i][f];
    }    
    source2.change.emit();
""")


# plotting inline:
slider1 = Slider(start=0, end=sizey, value=int(sizey/2), step=1, title="Horizontal line position", callback=callback1)
callback1.args["horizontalPosSlider"] = slider1
callback1.args["img"] = doseimg

slider2 = Slider(start=0, end=sizex, value=int(sizex/2), step=1, title="Vertical line position", callback=callback2)
callback2.args["verticalPosSlider"] = slider2
callback2.args["img"] = doseimg


# Organizing the graphs:
grid = gridplot([[p1, p1b],[slider1,slider2],[p2, p3]])

show(grid)

Image dimension (in pixels): 291 x 298
Dose max: 850 cGy
